In [1]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

np.random.seed(881)

# Define the model that generates pair simulations.
yuima = importr("yuima")
n_ou_sim_string = """
n_sim_ou = function(random_seed, num_sim,
                    mu11, mu12, mu21, mu22, sigma11, sigma12, sigma21, sigma22,
                    xinit_vec, T0, T, length){

  set.seed(random_seed)

  drift = c("mu11*t-mu12*X1", "mu21*t-mu22*X2")
  diffusion = matrix(c("exp(sigma11)", "exp(sigma12)", "exp(sigma21)", "exp(sigma22)"), 2, 2, byrow=TRUE)
  ou_model = setModel(drift=drift, diffusion=diffusion, 
                        time.variable = "t",
                        state.var=c("X1","X2"), solve.variable=c("X1","X2"))

  newsamp = setSampling(Initial=T0, Terminal=T, n=length)

  n_sim_ou_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    ou_sim = simulate(ou_model, 
                      true.par=list(
                        mu11=mu11, mu12=mu12, mu21=mu21, mu22=mu22, 
                        sigma11=sigma11, sigma12=sigma12, sigma21=sigma21, sigma22=sigma22), 
                      xinit=xinit_vec[i], sampling=newsamp)
    original_data = ou_sim@data@original.data
    one_sim_ou = data.frame(original_data[,1], original_data[,2])
    colnames(one_sim_ou) = c('series1', 'series2')
    n_sim_ou_data[, (2*i-1):(2*i)] = one_sim_ou
  }
  return(n_sim_ou_data)
}
"""

n_ou_sim = SignatureTranslatedAnonymousPackage(n_ou_sim_string, "n_ou_sim")
def n_ou_simulation(random_seed, num_sim,
                    mu11, mu12, mu21, mu22, sigma11, sigma12, sigma21, sigma22,
                    xinit_vec, T0, T, length):
    """num_sim simulations of bivariate Ornstein-Uhlenbeck process,
    length = length of one series
    """
    n_ou_sim_data = pd.DataFrame(
        n_ou_sim.n_sim_ou(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu12=mu12, mu21=mu21, mu22=mu22,
                              sigma11=sigma11, sigma12=sigma12, sigma21=sigma21, sigma22=sigma22,
                              xinit_vec=xinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_ou_sim_data

def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return


def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef


def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]
    sq_return_series1 = return_series1**2
    sq_return_series2 = return_series2**2

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
       
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series2.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values #8(8)
    
    
    
    # Autocorrelation of the 2 return series with 3 lags respectively
    autocorr1_lag_1 = return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr1_lag_2 = return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr1_lag_3 = return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr2_lag_1 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr2_lag_2 = return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr2_lag_3 = return_series2.apply(lambda x: x.autocorr(lag=3)) #6(14)
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(21)
    
    
    
    # Autocorrelation of the 2 squared returns with 3 lags respectively
    autocorr_sqreturn_1_lag_1 = sq_return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr_sqreturn_1_lag_2 = sq_return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr_sqreturn_1_lag_3 = sq_return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr_sqreturn_2_lag_1 = sq_return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr_sqreturn_2_lag_2 = sq_return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr_sqreturn_2_lag_3 = sq_return_series2.apply(lambda x: x.autocorr(lag=3))#6(27)
    
    # Cross-correlation between squared returns series
    corr_sqts1_lag_0 = []
    corr_sqts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_sqts1_lag_2 = []
    corr_sqts1_lag_3 = []
    corr_sqts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_sqts2_lag_2 = []
    corr_sqts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_sqts1_lag_0.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 0))
        corr_sqts1_lag_1.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 1))
        corr_sqts1_lag_2.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 2))
        corr_sqts1_lag_3.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 3))
        corr_sqts2_lag_1.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 1))
        corr_sqts2_lag_2.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 2))
        corr_sqts2_lag_3.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 3))
    corr_sqts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_sqts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_sqts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_sqts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_sqts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_sqts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_sqts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(34)
    
    
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, #8(8)
                               
                               autocorr1_lag_1, autocorr1_lag_2, autocorr1_lag_3,
                               autocorr2_lag_1, autocorr2_lag_2, autocorr2_lag_3,#6(14)
                               
                               corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3, #7(21)
                               
                               autocorr_sqreturn_1_lag_1, autocorr_sqreturn_1_lag_2, autocorr_sqreturn_1_lag_3,
                               autocorr_sqreturn_2_lag_1, autocorr_sqreturn_2_lag_2, autocorr_sqreturn_2_lag_3,#6(27)
                               
                               corr_sqts1_lag_0,
                               corr_sqts1_lag_1, corr_sqts1_lag_2, corr_sqts1_lag_3,
                               corr_sqts2_lag_1, corr_sqts2_lag_2, corr_sqts2_lag_3])#7(34)
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        
        'return_autocorrelation_ts1_lag1', 'return_autocorrelation_ts1_lag2', 'return_autocorrelation_ts1_lag3',
        'return_autocorrelation_ts2_lag1', 'return_autocorrelation_ts2_lag2', 'return_autocorrelation_ts2_lag3',
        
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        
        'sqreturn_autocorrelation_ts1_lag1', 'sqreturn_autocorrelation_ts1_lag2', 'sqreturn_autocorrelation_ts1_lag3',
        'sqreturn_autocorrelation_ts2_lag1', 'sqreturn_autocorrelation_ts2_lag2', 'sqreturn_autocorrelation_ts2_lag3',
    
        'sqreturn_correlation_ts1_lag_0',
        'sqreturn_correlation_ts1_lag_1', 'sqreturn_correlation_ts1_lag_2', 'sqreturn_correlation_ts1_lag_3', 
        'sqreturn_correlation_ts2_lag_1', 'sqreturn_correlation_ts2_lag_2', 'sqreturn_correlation_ts2_lag_3']
    
    return stats_data


def loss_function(params):

    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)

    n_real_log_price = n_ou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=mu11, mu12=mu12, 
        mu21=mu21, mu22=mu22,
        sigma11=sigma11, sigma12=sigma12, 
        sigma21=sigma21, sigma22=sigma22,
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    n_real_price = log_price_to_price(n_real_log_price)
    n_real_return = price_to_return(n_real_price)
    n_real_stats = cal_stats(n_real_return, n_real_price)
    
    
    n_sim_log_price = n_ou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu12=params[1], 
        mu21=params[2], mu22=params[3],
        sigma11=params[4], sigma12=params[5], 
        sigma21=params[6], sigma22=params[7],
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    n_sim_price = log_price_to_price(n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_sim_return, n_sim_price)


    moment_loss = np.abs(n_real_stats - n_sim_stats)
    sum_loss = np.sum(moment_loss)
    
    sum_loss[6] = sum_loss[6]/10 
    sum_loss[7] = sum_loss[7]/10 
    
    loss = np.sum(sum_loss)
    
    print(sum_loss)
    print(loss)
    print('----------')

    return loss



mu11 = 0.5689102
mu12 = 0.1308214 
mu21 = 0.6956711 
mu22 = 0.1349717
sigma11 = -3.3933278
sigma12 = -1.2515663 
sigma21 = -1.3669886
sigma22 = -2.9761180   


real_price = pd.read_csv(real_data_folder + "pair_prices_cal.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv(real_data_folder + "pair_returns_cal.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
num_sim, T0, T, length = real_stats.shape[0], 0, 2, real_price.shape[0]


initial0 = [1, 1, 1, 1, -1, -1, -1, -1]
begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(0, None), (0, None), (0, None), (0, None),
                       (None, None), (None, None), (None, None), (None, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

[1]  1  1  1  1 -1 -1 -1 -1

return_mean1                         101.773776
return_mean2                          96.352766
return_sd1                           381.295073
return_sd2                           371.304942
return_skew1                         143.123570
return_skew2                         156.317882
return_kurtosis1                     156.010694
return_kurtosis2                     173.663675
return_autocorrelation_ts1_lag1       15.674237
return_autocorrelation_ts1_lag2       15.342536
return_autocorrelation_ts1_lag3       15.466070
return_autocorrelation_ts2_lag1       16.444044
return_autocorrelation_ts2_lag2       14.579628
return_autocorrelation_ts2_lag3       15.043308
return_correlation_ts1_lag_0         166.457237
return_correlation_ts1_lag_1          13.823015
return_correlation_ts1_lag_2          14.884088
return_correlation_ts1_lag_3          14.763330
return_correlation_ts2_lag_1          15.423882
return_correlation_ts2_lag_2          13.126919
return_corr

return_mean1                          83.242650
return_mean2                          96.434336
return_sd1                           393.947210
return_sd2                           374.998504
return_skew1                         143.464128
return_skew2                         150.969501
return_kurtosis1                     156.877963
return_kurtosis2                     174.577136
return_autocorrelation_ts1_lag1       19.590129
return_autocorrelation_ts1_lag2       19.237358
return_autocorrelation_ts1_lag3       17.405106
return_autocorrelation_ts2_lag1       16.113366
return_autocorrelation_ts2_lag2       15.111317
return_autocorrelation_ts2_lag3       15.165423
return_correlation_ts1_lag_0         165.311201
return_correlation_ts1_lag_1          14.542175
return_correlation_ts1_lag_2          15.573896
return_correlation_ts1_lag_3          15.264615
return_correlation_ts2_lag_1          15.904441
return_correlation_ts2_lag_2          14.535336
return_correlation_ts2_lag_3          14

return_mean1                          37.278289
return_mean2                          98.346700
return_sd1                           391.683390
return_sd2                           376.816250
return_skew1                         144.794129
return_skew2                         156.216885
return_kurtosis1                     155.818317
return_kurtosis2                     173.449691
return_autocorrelation_ts1_lag1       18.756617
return_autocorrelation_ts1_lag2       16.655854
return_autocorrelation_ts1_lag3       15.556820
return_autocorrelation_ts2_lag1       16.876208
return_autocorrelation_ts2_lag2       15.132023
return_autocorrelation_ts2_lag3       13.929848
return_correlation_ts1_lag_0         166.076295
return_correlation_ts1_lag_1          15.562595
return_correlation_ts1_lag_2          15.000337
return_correlation_ts1_lag_3          14.399961
return_correlation_ts2_lag_1          16.565604
return_correlation_ts2_lag_2          13.546716
return_correlation_ts2_lag_3          13

return_mean1                          36.699819
return_mean2                          95.075463
return_sd1                           388.607665
return_sd2                           375.968189
return_skew1                         141.979980
return_skew2                         154.840375
return_kurtosis1                     156.285324
return_kurtosis2                     173.943707
return_autocorrelation_ts1_lag1       20.166055
return_autocorrelation_ts1_lag2       16.421477
return_autocorrelation_ts1_lag3       15.428939
return_autocorrelation_ts2_lag1       16.733163
return_autocorrelation_ts2_lag2       15.391616
return_autocorrelation_ts2_lag3       15.115655
return_correlation_ts1_lag_0         166.076709
return_correlation_ts1_lag_1          15.843140
return_correlation_ts1_lag_2          14.163066
return_correlation_ts1_lag_3          14.395253
return_correlation_ts2_lag_1          16.388880
return_correlation_ts2_lag_2          13.482025
return_correlation_ts2_lag_3          14

return_mean1                         826.036584
return_mean2                          99.773416
return_sd1                           483.008604
return_sd2                           377.189795
return_skew1                         145.945588
return_skew2                         153.291683
return_kurtosis1                     158.181921
return_kurtosis2                     174.635892
return_autocorrelation_ts1_lag1       64.851161
return_autocorrelation_ts1_lag2       61.373659
return_autocorrelation_ts1_lag3       58.459055
return_autocorrelation_ts2_lag1       18.008735
return_autocorrelation_ts2_lag2       15.596525
return_autocorrelation_ts2_lag3       15.075525
return_correlation_ts1_lag_0         147.130186
return_correlation_ts1_lag_1          20.259818
return_correlation_ts1_lag_2          19.529469
return_correlation_ts1_lag_3          18.546942
return_correlation_ts2_lag_1          21.147218
return_correlation_ts2_lag_2          17.755606
return_correlation_ts2_lag_3          16

...

return_mean1                          21.541441
return_mean2                          22.852814
return_sd1                           166.641786
return_sd2                           181.065978
return_skew1                         143.018040
return_skew2                         155.568446
return_kurtosis1                     156.291584
return_kurtosis2                     173.659844
return_autocorrelation_ts1_lag1       15.289539
return_autocorrelation_ts1_lag2       14.814857
return_autocorrelation_ts1_lag3       15.196418
return_autocorrelation_ts2_lag1       16.496986
return_autocorrelation_ts2_lag2       14.760777
return_autocorrelation_ts2_lag3       14.020622
return_correlation_ts1_lag_0          31.053994
return_correlation_ts1_lag_1          13.505957
return_correlation_ts1_lag_2          14.451875
return_correlation_ts1_lag_3          14.661911
return_correlation_ts2_lag_1          15.247565
return_correlation_ts2_lag_2          12.866846
return_correlation_ts2_lag_3          14

return_mean1                          22.096952
return_mean2                          23.446775
return_sd1                           169.047187
return_sd2                           182.436979
return_skew1                         142.843650
return_skew2                         154.772978
return_kurtosis1                     156.733477
return_kurtosis2                     173.564536
return_autocorrelation_ts1_lag1       14.572776
return_autocorrelation_ts1_lag2       14.941668
return_autocorrelation_ts1_lag3       14.294822
return_autocorrelation_ts2_lag1       16.739392
return_autocorrelation_ts2_lag2       15.198150
return_autocorrelation_ts2_lag3       14.715437
return_correlation_ts1_lag_0          31.026391
return_correlation_ts1_lag_1          14.087263
return_correlation_ts1_lag_2          14.560714
return_correlation_ts1_lag_3          14.647635
return_correlation_ts2_lag_1          15.458199
return_correlation_ts2_lag_2          14.066209
return_correlation_ts2_lag_3          14

return_mean1                          21.611050
return_mean2                          21.592345
return_sd1                           167.512907
return_sd2                           181.301654
return_skew1                         148.869096
return_skew2                         153.089800
return_kurtosis1                     156.620961
return_kurtosis2                     173.698725
return_autocorrelation_ts1_lag1       15.829820
return_autocorrelation_ts1_lag2       13.671983
return_autocorrelation_ts1_lag3       14.262166
return_autocorrelation_ts2_lag1       16.847529
return_autocorrelation_ts2_lag2       15.725621
return_autocorrelation_ts2_lag3       13.847343
return_correlation_ts1_lag_0          31.277113
return_correlation_ts1_lag_1          14.508229
return_correlation_ts1_lag_2          13.562171
return_correlation_ts1_lag_3          14.546580
return_correlation_ts2_lag_1          15.532008
return_correlation_ts2_lag_2          14.120823
return_correlation_ts2_lag_3          13

return_mean1                          21.803660
return_mean2                          21.505312
return_sd1                           167.572555
return_sd2                           181.802075
return_skew1                         142.650306
return_skew2                         157.167862
return_kurtosis1                     157.147338
return_kurtosis2                     174.201372
return_autocorrelation_ts1_lag1       15.480974
return_autocorrelation_ts1_lag2       14.189088
return_autocorrelation_ts1_lag3       13.892045
return_autocorrelation_ts2_lag1       16.838357
return_autocorrelation_ts2_lag2       15.234986
return_autocorrelation_ts2_lag3       15.483072
return_correlation_ts1_lag_0          31.891621
return_correlation_ts1_lag_1          13.875863
return_correlation_ts1_lag_2          13.353998
return_correlation_ts1_lag_3          13.924711
return_correlation_ts2_lag_1          15.039984
return_correlation_ts2_lag_2          13.761550
return_correlation_ts2_lag_3          14

return_mean1                          21.405741
return_mean2                          21.423195
return_sd1                           166.896272
return_sd2                           182.378180
return_skew1                         144.379033
return_skew2                         152.827761
return_kurtosis1                     156.951260
return_kurtosis2                     173.792024
return_autocorrelation_ts1_lag1       16.039236
return_autocorrelation_ts1_lag2       13.494752
return_autocorrelation_ts1_lag3       14.509710
return_autocorrelation_ts2_lag1       16.327491
return_autocorrelation_ts2_lag2       15.285075
return_autocorrelation_ts2_lag3       14.975295
return_correlation_ts1_lag_0          32.325574
return_correlation_ts1_lag_1          14.762613
return_correlation_ts1_lag_2          14.903025
return_correlation_ts1_lag_3          14.324068
return_correlation_ts2_lag_1          15.337516
return_correlation_ts2_lag_2          13.407896
return_correlation_ts2_lag_3          13

In [ ]:
print(params)